In [41]:
from matplotlib import pyplot as plt
from matplotlib import animation, rc
from matplotlib.offsetbox import AnchoredText
from IPython.display import HTML
import numpy as np
from scipy.optimize import least_squares

In [4]:
def circle_intersection(circle1, circle2):
    # Copied from https://gist.github.com/xaedes/974535e71009fa8f090e
    # which is based on http://paulbourke.net/geometry/circlesphere/
    '''
    @summary: calculates intersection points of two circles
    @param circle1: tuple(x,y,radius)
    @param circle2: tuple(x,y,radius)
    @result: tuple of intersection points (which are (x,y) tuple)
    '''
    # return self.circle_intersection_sympy(circle1,circle2)
    x1,y1,r1 = circle1
    x2,y2,r2 = circle2
    # http://stackoverflow.com/a/3349134/798588
    dx,dy = x2-x1,y2-y1
    d = np.sqrt(dx*dx+dy*dy)
    if d > r1+r2:
        return None # no solutions, the circles are separate
    if d < abs(r1-r2):
        return None # no solutions because one circle is contained within the other
    if d == 0 and r1 == r2:
        return None # circles are coincident and there are an infinite number of solutions

    a = (r1*r1-r2*r2+d*d)/(2*d)
    h = np.sqrt(r1*r1-a*a)
    xm = x1 + a*dx/d
    ym = y1 + a*dy/d
    xs1 = xm + h*dy/d
    xs2 = xm - h*dy/d
    ys1 = ym - h*dx/d
    ys2 = ym + h*dx/d

    return (xs1,ys1),(xs2,ys2)

In [37]:
def initialize_animation(title, point_coords, links, xlim, ylim, show_static_plot=False):
    # Draw the initial link configuration
    points_drawn = []
    lines_drawn = []
    points_text_drawn = []
    line_text_drawn = []
    foot_trajectory_x = []
    foot_trajectory_y = []

    plt.clf()
    plt.close()

    fig, ax = plt.subplots(figsize=(10, 10))
    
    circle1 = plt.Circle((0, 0), 5, color='#faafcd', fill=True)
    circle2 = plt.Circle((0, 0), 5, color='#999999', fill=False)
    circle3 = plt.Circle((0, 0), 0.5, color='#999999', fill=True)
    circle4 = plt.Circle((0, 0), 0.5, color='#000000', fill=False)
    ax.add_patch(circle1)
    ax.add_patch(circle2)
    ax.add_patch(circle3)
    ax.add_patch(circle4)
    ax.text(-3, 2, 'Motor')


    ax.set_xlim(xlim)
    ax.set_ylim(ylim)

    for ctr, pos in enumerate(point_coords):
        pt, = ax.plot(pos[0], pos[1], '*')
        points_drawn.append(pt)
        txt = ax.text(pos[0], pos[1], str(ctr))
        points_text_drawn.append(txt)

    for link in links:
        from_point = point_coords[link[0]]
        to_point = point_coords[link[1]]

        line, = ax.plot([from_point[0], to_point[0]], [from_point[1], to_point[1]])
        lines_drawn.append(line)
        txt = ax.text((from_point[0]+to_point[0])/2.0, (from_point[1]+to_point[1])/2.0, '['+str(link)+']')
        line_text_drawn.append(txt)

    draw_foot_trajectory, = ax.plot([], [], color='red', linewidth=2, alpha=0.5);

    text_box = AnchoredText('Frame 0', frameon=True, loc=4, pad=0.5)
    plt.setp(text_box.patch, facecolor='white', alpha=0.5)
    plt.gca().add_artist(text_box)

    ax.set_aspect('equal', 'box')
    
    title_box = AnchoredText(title, frameon=False, loc='upper left', pad=0.5, prop=dict(fontweight="bold", fontsize=18))
    plt.setp(title_box.patch, facecolor='white', alpha=0.5)
    plt.gca().add_artist(title_box)
    

    plt.axvline(x=point_coords[0][0], linewidth=1, linestyle='dashed', color='#999999')
    if show_static_plot:
        plt.show()
    else:
        plt.close()
    return fig, points_drawn, lines_drawn, points_text_drawn, line_text_drawn, draw_foot_trajectory, text_box, foot_trajectory_x, foot_trajectory_y

def animate(frame_nr, leg_link_params, anim_initialization, nr_frames, max_angle):
    
    fig, points_drawn, lines_drawn, points_text_drawn, line_text_drawn, draw_foot_trajectory, text_box, foot_trajectory_x, foot_trajectory_y = anim_initialization

    # angle of joint
    frame_progress = frame_nr/float(nr_frames-1)
    i = min_angle + frame_progress*(max_angle-min_angle)
    
    point_coords, links = get_point_coordinates_from_parameters(leg_link_params, motor_angle=i)
    if point_coords is None:
        return []
    
    for ctr, pos in enumerate(point_coords):
        points_drawn[ctr].set_data(pos[0], pos[1])
        points_text_drawn[ctr].set_position((pos[0], pos[1]))
        if(ctr == foot_id):
            foot_trajectory_x.append(pos[0])
            foot_trajectory_y.append(pos[1])
            draw_foot_trajectory.set_data(foot_trajectory_x, foot_trajectory_y)
    
    ctr1 = 0
    for link in links:
        from_point = point_coords[link[0]]
        to_point = point_coords[link[1]]

        lines_drawn[ctr1].set_data([from_point[0], to_point[0]], [from_point[1], to_point[1]])
        line_text_drawn[ctr1].set_position(((from_point[0]+to_point[0])/2.0, (from_point[1]+to_point[1])/2.0))
        ctr1 += 1                
           

    text_box.txt.set_text(f"θ: {i}")

    entities_to_draw = [l for l in lines_drawn]
    entities_to_draw.extend(points_drawn)
    entities_to_draw.extend(points_text_drawn)
    entities_to_draw.extend(line_text_drawn)
    entities_to_draw.append(draw_foot_trajectory)
    entities_to_draw.append(text_box)
    return entities_to_draw

def animate_leg(min_angle, max_angle, leg_params, title, filename=None, xlim=( -30, 30), ylim=(-50, 20)):
    nr_frames = max_angle-min_angle+1
    
    point_coords, links = get_point_coordinates_from_parameters(leg_params, motor_angle=min_angle)

    anim_initialization = initialize_animation(title, point_coords, links, xlim=xlim, ylim=ylim)    
    anim = animation.FuncAnimation(anim_initialization[0], animate,
                                   frames=nr_frames, interval=20, 
                                   blit=True, fargs=(leg_params, anim_initialization, nr_frames, max_angle))

    if filename is not None:
        anim.save(filename)
    return anim, HTML(anim.to_jshtml())


In [6]:
def get_point_1(link_length, link_angle_radians):
    # Location of hip linkage (point 1)
    hip_linkage_x = link_length * np.cos(link_angle_radians)
    hip_linkage_y = link_length * np.sin(link_angle_radians)
    return np.array([hip_linkage_x, hip_linkage_y])

In [7]:
def get_point_3(link_length, motor_angle):
    # Location of knee joint (point 3)
    knee_joint_x = link_length * np.sin(np.radians(-270-motor_angle))
    knee_joint_y = link_length * np.cos(np.radians(-270-motor_angle))
    return np.array([knee_joint_x, knee_joint_y])

In [8]:
def get_point_2(link_length_knee_to_linkage, linkage_length, knee_joint_coords, hip_linkage_coords):
    # Location of hip-linkage at knee joint (point 2)
    c1 = (knee_joint_coords[0], knee_joint_coords[1], link_length_knee_to_linkage)
    c2 = (hip_linkage_coords[0], hip_linkage_coords[1], linkage_length)
    intersections = circle_intersection(c1, c2)

    if intersections is None:
        return None
    
    # Keep the point that is at the right side of the knee joint
    if intersections[0][0] >= knee_joint_coords[0]:
        knee_linkage_x = intersections[0][0]
        knee_linkage_y = intersections[0][1]
    else:
        knee_linkage_x = intersections[1][0]
        knee_linkage_y = intersections[1][1]

    return np.array([knee_linkage_x, knee_linkage_y])

In [9]:
def get_point_4(link_length, link_angle_radians, knee_joint_coords, knee_linkage_coords):
    # Location of ankle (point 4)
    direction = knee_joint_coords - knee_linkage_coords
    direction = direction/np.linalg.norm(direction)
    ankle_location = knee_joint_coords + link_length * direction
    cos_angle = np.cos(link_angle_radians)
    sin_angle = np.sin(link_angle_radians)
    rotmat = np.array([[cos_angle, -sin_angle], [sin_angle, cos_angle]])
    ankle_location = rotmat.dot([ankle_location[0]-knee_joint_coords[0], ankle_location[1]-knee_joint_coords[1]]) + np.array([knee_joint_coords[0], knee_joint_coords[1]])
    return ankle_location

In [10]:
def get_point_5(link_length, knee_joint_coords, ankle_joint_coords):
    # Location of foot (point 5)
    direction = knee_joint_coords # (knee_joint_coords - motor_joint_coords), where motor_joint_coords=[0, 0]
    direction = direction/np.linalg.norm(direction)
    foot_location = ankle_joint_coords + link_length * direction
    return foot_location

In [11]:
def get_point_6(link_length, knee_joint_coords, ankle_joint_coords):
    # Location of foot (point 5)
    direction = -knee_joint_coords # (knee_joint_coords - motor_joint_coords), where motor_joint_coords=[0, 0]
    direction = direction/np.linalg.norm(direction)
    foot_linkage_location = ankle_joint_coords + link_length * direction
    return foot_linkage_location

In [12]:
def get_point_7(link_length, knee_joint_coords):
    # Location of foot (point 5)
    direction = -knee_joint_coords # (knee_joint_coords - motor_joint_coords), where motor_joint_coords=[0, 0]
    direction = direction/np.linalg.norm(direction)
    foot_linkage_location = knee_joint_coords + link_length * direction
    return foot_linkage_location

In [13]:
def get_point_coordinates_from_parameters(leg_link_params, motor_angle):
    point_1 = get_point_1(leg_link_params['link_0_1_length'], np.radians(leg_link_params['link_0_1_angle']))
    point_3 = get_point_3(leg_link_params['link_0_3_length'], motor_angle)
    point_2 = get_point_2(leg_link_params['link_3_2_length'], leg_link_params['link_1_2_length'], point_3, point_1)
    if point_2 is None: 
        return None, None
    point_4 = get_point_4(leg_link_params['link_3_4_length'], np.radians(leg_link_params['link_3_2_angle']), point_3, point_2)
    point_5 = get_point_5(leg_link_params['link_4_5_length'], point_3, point_4)
    point_6 = get_point_6(leg_link_params['link_4_6_length'], point_3, point_4)
    point_7 = get_point_7(leg_link_params['link_4_6_length'], point_3)
    links = [(0, 1), (1, 2), (2, 3), (0, 3), (3, 4), (4, 5), (4, 6), (6, 7)]
    return [np.array([0.0, 0.0]), point_1, point_2, point_3, point_4, point_5, point_6, point_7], links

In [14]:
foot_id = 5 # Point ID of the foot
motor_angle = 270 # Motor angle when the leg is at rest
min_angle = 285
max_angle = 337

param_dict_keys = ['link_0_1_length', 'link_0_1_angle', 'link_0_3_length', 'link_3_4_length', 'link_3_2_length', 'link_1_2_length', 'link_3_2_angle', 'link_4_5_length', 'link_4_6_length']

leg_link_params = {
    'link_0_1_length': 10.0,
    'link_0_1_angle': 45.0,
    'link_0_3_length': 20.0,
    'link_3_4_length': 20.0,
    'link_3_2_length': 6.0,
    'link_1_2_length': 25.0,
    'link_3_2_angle': 0.0,  # Angle between link_4_3 and link 2_3
    'link_4_5_length': 10.0,
    'link_4_6_length': 3.0,
}

param_bounds = {
        'link_0_1_length': [3, 10],
        'link_0_1_angle': [-80, 80],
        'link_0_3_length': [15, 30],
        'link_3_4_length': [15, 30],
        'link_3_2_length': [5, 20],
        'link_1_2_length': [10, 35],
        'link_3_2_angle': [-45, 45],
        'link_4_5_length': [5, 30],
        'link_4_6_length': [0, 10]
}
bounds = ([param_bounds[key][0] for key in param_dict_keys], [param_bounds[key][1] for key in param_dict_keys])

In [15]:
def flatten_params(param_dict):
    return np.array([leg_link_params[n] for n in param_dict_keys])

def unflatten_params(param_vector):
    return {n: param_vector[i] for i,n in enumerate(param_dict_keys)}

In [28]:
def loss_func_residuals(params, *args, **kwargs):
    # Get simulation data by varying the motor angle from 180 to 360 degree (i.e. doing a full leg sweep)
    param_dict = unflatten_params(params)
    residuals = np.zeros(max_angle-min_angle+1)    
    
    for motor_angle in range(min_angle, max_angle+1):
        point_coords, links = get_point_coordinates_from_parameters(param_dict, motor_angle)        
        if point_coords is None:
            residuals[motor_angle-min_angle] = 1000
            continue
        # Get the coordinate of the foot endpoint
        foot_coordinates = point_coords[foot_id]
        # Calculate the distance between the foot coordinate and the vertical line intersecting the 
        # origin (i.e. the motor centroid)
        residuals[motor_angle-min_angle] = abs(foot_coordinates[0])

    return residuals

In [18]:
initial_guess = [leg_link_params[key] for key in param_dict_keys]

In [19]:
result = least_squares(loss_func_residuals, initial_guess, bounds=bounds, loss='soft_l1', jac='3-point', tr_solver='exact')

In [20]:
result.success

True

In [21]:
new_leg_link_params = {key: result.x[i] for i, key in enumerate(param_dict_keys)}

In [22]:
leg_link_params

{'link_0_1_length': 10.0,
 'link_0_1_angle': 45.0,
 'link_0_3_length': 20.0,
 'link_3_4_length': 20.0,
 'link_3_2_length': 6.0,
 'link_1_2_length': 25.0,
 'link_3_2_angle': 0.0,
 'link_4_5_length': 10.0,
 'link_4_6_length': 3.0}

In [23]:
new_leg_link_params

{'link_0_1_length': 9.999999999999998,
 'link_0_1_angle': 19.580054918230694,
 'link_0_3_length': 15.000000005546704,
 'link_3_4_length': 18.607448673159602,
 'link_3_2_length': 5.000000000000001,
 'link_1_2_length': 14.706574661004888,
 'link_3_2_angle': 34.70245580213259,
 'link_4_5_length': 5.0000002443567535,
 'link_4_6_length': 3.0}

In [46]:
animation_obj, html_animation = animate_leg(min_angle, max_angle-1, leg_link_params, title="Initial estimate", xlim=(-20, 30), ylim=(-40, 10))
html_animation

In [48]:
animation_obj, html_animation = animate_leg(min_angle, max_angle, new_leg_link_params, title="Optimized leg design", xlim=(-20, 30), ylim=(-40, 10))
html_animation

In [26]:
for k, v in new_leg_link_params.items():
    print(k, v*10 if 'angle' not in k else v)

link_0_1_length 99.99999999999999
link_0_1_angle 19.580054918230694
link_0_3_length 150.00000005546704
link_3_4_length 186.07448673159604
link_3_2_length 50.00000000000001
link_1_2_length 147.06574661004888
link_3_2_angle 34.70245580213259
link_4_5_length 50.00000244356754
link_4_6_length 30.0
